In [2]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics.pairwise import cosine_similarity
from groq import Groq
from sentence_transformers import SentenceTransformer
import json
import re
from typing import Dict, List, Any
import pandas_gbq

import yfinance as yf
import matplotlib.pyplot as plt
import pandas as pd

import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [3]:
def load_table_from_bigquery(dataset_id, table_id, project_id):
    """Load a table from BigQuery."""

    query = f"SELECT * FROM `{dataset_id}.{table_id}`"
    df = pandas_gbq.read_gbq(query, project_id=project_id)
    return df

df_data = load_table_from_bigquery(dataset_id='stock_data', table_id='stock_data', project_id="capable-arbor-293714")
df_data

Downloading: 100%|██████████|


Ticker  Closing_Price  All_Time_High  Percent_From_All_Time_High  \
0     CTVA          76.45          77.12                       -0.87   
1       CF          97.12         111.25                      -12.70   
2      MOS          37.31          72.25                      -48.36   
3      VMC         266.45         291.14                       -8.48   
4      MLM         559.09         617.09                       -9.40   
..     ...            ...            ...                         ...   
495    PNW          89.62          94.52                       -5.19   
496    ATO         151.99         161.76                       -6.04   
497     NI          39.00          40.94                       -4.74   
498    AWK         141.02         175.80                      -19.78   
499    CEG         312.84         346.32                       -9.67   

     Percent_Difference_200_Day_Moving_Average  24_Hour_Percent_Change  \
0                                        22.55                   -0.17   
1                                        14.76                    2.03   
2                                        33.23                   -1.01   
3                                         2.86                   -0.21   
4                                         4.57                    0.50   
..                                         ...                     ...   
495                                       1.16                   -0.53   
496                                       4.04                   -0.52   
497                                       4.38                   -1.59   
498                                       3.67                    0.76   
499                                      20.13                   -1.70   

     7_Day_Percent_Change  30_Day_Percent_Change  Annualized_Return  \
0                    2.89                  11.73              21.06   
1                    7.09                   9.23              26.27   
2                    6.05                   7.21              23.27   
3                    3.69                  -1.75              15.49   
4                    3.41                  -0.85              18.70   
..                    ...                    ...                ...   
495                  0.73                  -0.30               6.58   
496                 -0.61                  -1.58               9.95   
497                 -1.54                   1.30              12.46   
498                  1.88                  -0.59               2.86   
499                 -3.00                   7.33              66.50   

     YTD_Return  ...        Country  \
0         36.39  ...  United States   
1         14.52  ...  United States   
2         55.37  ...  United States   
3          4.68  ...  United States   
4          9.84  ...  United States   
..          ...  ...            ...   
495        8.43  ...  United States   
496       11.16  ...  United States   
497        8.84  ...  United States   
498       15.25  ...  United States   
499       29.37  ...  United States   

                                      Business_Summary  Dividend_Yield  \
0    Corteva, Inc. operates in the agriculture busi...            0.91   
1    CF Industries Holdings, Inc., together with it...            2.17   
2    The Mosaic Company, through its subsidiaries, ...            2.41   
3    Vulcan Materials Company produces and supplies...            0.75   
4    Martin Marietta Materials, Inc., a natural res...            0.58   
..                                                 ...             ...   
495  Pinnacle West Capital Corporation, through its...            4.00   
496  Atmos Energy Corporation, together with its su...            2.26   
497  NiSource Inc., an energy holding company, oper...            2.78   
498  American Water Works Company, Inc., through it...            2.38   
499  Constellation Energy Corporation produces and ...            0.48   

     Trailing_PE  Forward_PE  Average_V

### Sector Returns

In [4]:
return_columns = ['Percent_From_All_Time_High', 'Percent_Difference_200_Day_Moving_Average', '24_Hour_Percent_Change', '7_Day_Percent_Change', '30_Day_Percent_Change', 'Annualized_Return', 'YTD_Return']
df_sector = df_data[['Ticker', 'Sector', 'Market_Cap'] + return_columns]

df_sector[return_columns] = df_sector[return_columns].mul(df_sector['Market_Cap'], axis=0)
df_sector = df_sector.groupby(['Sector'], as_index=False).sum(numeric_only=True)

df_sector[return_columns] = df_sector[return_columns].div(df_sector['Market_Cap'], axis=0)
df_sector = df_sector.sort_values('Market_Cap', ascending=False).reset_index(drop=True)
df_sector

/var/folders/rx/jl4f7yr95xd03cgb4sg2w99h0000gn/T/ipykernel_75055/399811760.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_sector[return_columns] = df_sector[return_columns].mul(df_sector['Market_Cap'], axis=0)


Sector      Market_Cap  Percent_From_All_Time_High  \
0               Technology  18638808328192                   -8.023938   
1   Communication Services   7939517619200                  -12.498298   
2       Financial Services   6802629931520                   -7.113686   
3        Consumer Cyclical   6057081841664                  -16.968857   
4               Healthcare   5070821544960                   -22.11017   
5              Industrials   4229096045568                   -9.034658   
6       Consumer Defensive   3342614905856                  -12.626961   
7                   Energy   1695611958784                  -15.083082   
8                Utilities   1250400309248                  -10.622756   
9              Real Estate   1115653005312                  -18.469047   
10         Basic Materials    916723806720                  -13.751937   

    Percent_Difference_200_Day_Moving_Average  24_Hour_Percent_Change  \
0                                   15.121653                0.386008   
1                                     7.87409               -0.744284   
2                                    9.291913               -0.936187   
3                                    4.019441               -0.605473   
4                                   -2.536253                0.435398   
5                                   10.357452                0.013739   
6                                    3.849421               -1.200872   
7                                    2.672888                2.777362   
8                                    5.003197               -1.051114   
9                                    0.395432               -0.151048   
10                                   5.124042                0.510911   

    7_Day_Percent_Change  30_Day_Percent_Change  Annualized_Return  YTD_Return  
0                2.28782              12.953239          27.384755   13.182901  
1               0.132291               5.281983          14.840135    5.509906  
2               1.426271               6.476808          16.325035   10.875263  
3               1.024985               3.977815          11.396316   -0.820858  
4               0.707079               4.283143          10.778219     2.81295  
5               2.444564               6.242358          21.323559   15.292506  
6               1.181709               0.607273          11.647513    9.062908  
7               3.468591               9.635983          22.474912    4.790646  
8                 0.0135               2.448605          14.904023   10.150757  
9               1.137009                 3.1898           8.643412    5.744211  
10              2.865865                6.83152          12.558485    14.73656

### Mag7 Returns

In [5]:
return_columns = ['Percent_From_All_Time_High', 'Percent_Difference_200_Day_Moving_Average', '24_Hour_Percent_Change', '7_Day_Percent_Change', '30_Day_Percent_Change', 'Annualized_Return', 'YTD_Return']
df_mag_7 = df_data[['Ticker', 'Sector', 'Market_Cap'] + return_columns]

df_mag_7 = df_mag_7[df_mag_7['Ticker'].isin(['NVDA', 'MSFT', 'AAPL', 'AMZN', 'GOOG', 'META', 'TSLA'])]

df_mag_7 = df_mag_7.sort_values('Market_Cap', ascending=False).reset_index(drop=True)
df_mag_7

Ticker                  Sector     Market_Cap  Percent_From_All_Time_High  \
0   NVDA              Technology  3902016061440                        0.00   
1   MSFT              Technology  3691147952128                       -0.45   
2   AAPL              Technology  3136667254784                      -18.73   
3   AMZN       Consumer Cyclical  2328813371392                       -9.38   
4   GOOG  Communication Services  2120451883008                      -15.47   
5   META  Communication Services  1812002242560                       -2.36   
6   TSLA       Consumer Cyclical   959234113536                      -37.94   

   Percent_Difference_200_Day_Moving_Average  24_Hour_Percent_Change  \
0                                      22.66                    1.11   
1                                      17.18                   -0.22   
2                                      -5.66                    0.03   
3                                       6.48                   -1.84   
4                                       0.61                   -1.35   
5                                      17.13                    0.32   
6                                      -5.51                    1.32   

   7_Day_Percent_Change  30_Day_Percent_Change  Annualized_Return  YTD_Return  
0                  3.21                  20.46              57.52       15.70  
1                 -0.17                   9.18              15.86       19.10  
2                  4.48                   4.30              14.52      -13.67  
3                  1.03                   8.01               5.50       -0.39  
4                  0.42                   1.97              15.16       -7.90  
5                 -0.75                  13.30              19.85       20.46  
6                 -8.59                 -12.68              21.42      -21.48

# Yahoo Finance API

In [6]:
moving_average = 200

df_historical_data = pd.DataFrame()
for ticker in df_mag_7['Ticker'].unique().tolist():
# Create a Ticker object
    ticker_symbol = ticker
    ticker = yf.Ticker(ticker_symbol)


    # Fetch historical market data
    df_hist = ticker.history(period="30y").reset_index()  # data for the last year

    df_hist[f'{moving_average}DMA'] = df_hist['Close'].rolling(window=moving_average).mean()

    df_hist.loc[df_hist[f'{moving_average}DMA'] < df_hist['Close'], f'Greater_than_{moving_average}_DMA'] = df_hist['Close']
    df_hist.loc[df_hist[f'{moving_average}DMA'] >= df_hist['Close'], f'Less_than_{moving_average}_DMA'] = df_hist['Close']

    # pct extension from {200}DMA
    df_hist['pct_extension'] = (df_hist['Close'] - df_hist[f'{200}DMA']) / df_hist[f'{200}DMA'] * 100
    df_hist.loc[df_hist['pct_extension'] >= 0, 'Greater_than_0'] = df_hist['pct_extension']
    df_hist.loc[df_hist['pct_extension'] < 0, 'Less_than_0'] = df_hist['pct_extension']
    df_hist['Ticker'] = ticker_symbol
    df_historical_data = pd.concat([df_historical_data, df_hist])

df_historical_data = df_historical_data[df_historical_data['Date'] >= '2015-01-01']
df_historical_data

Date        Open        High         Low  \
4012 2015-01-02 00:00:00-05:00    0.483066    0.486665    0.475386   
4013 2015-01-05 00:00:00-05:00    0.483066    0.484505    0.472747   
4014 2015-01-06 00:00:00-05:00    0.475626    0.476106    0.460028   
4015 2015-01-07 00:00:00-05:00    0.463868    0.467947    0.457868   
4016 2015-01-08 00:00:00-05:00    0.464588    0.479466    0.464348   
...                        ...         ...         ...         ...   
3774 2025-07-01 00:00:00-04:00  298.459991  305.890015  293.209991   
3775 2025-07-02 00:00:00-04:00  312.630005  316.829987  303.820007   
3776 2025-07-03 00:00:00-04:00  317.989990  318.450012  312.760010   
3777 2025-07-07 00:00:00-04:00  291.369995  296.149994  288.769989   
3778 2025-07-08 00:00:00-04:00  297.000000  304.049988  294.350006   

           Close     Volume  Dividends  Stock Splits      200DMA  \
4012    0.483066  113680000        0.0           0.0    0.452383   
4013    0.474906  197952000        0.0           0.0    0.452559   
4014    0.460508  197764000        0.0           0.0    0.452666   
4015    0.459308  321808000        0.0           0.0    0.452778   
4016    0.476586  283780000        0.0           0.0    0.452976   
...          ...        ...        ...           ...         ...   
3774  300.709991  145085700        0.0           0.0  313.644300   
3775  315.649994  119483700        0.0           0.0  314.073500   
3776  315.350006   58042300        0.0           0.0  314.498800   
3777  293.940002  131177900        0.0           0.0  314.834600   
3778  297.809998  102736500        0.0           0.0  315.184300   

      Greater_than_200_DMA  Less_than_200_DMA  pct_extension  Greater_than_0  \
4012              0.483066                NaN       6.782365        6.782365   
4013              0.474906                NaN       4.938013        4.938013   
4014              0.460508                NaN       1.732390        1.732390   
4015              0.459308                NaN       1.442241        1.442241   
4016              0.476586                NaN       5.212154        5.212154   
...                    ...                ...            ...             ...   
3774                   NaN         300.709991      -4.123878             NaN   
3775            315.649994                NaN       0.501951        0.501951   
3776            315.350006                NaN       0.270655        0.270655   
3777                   NaN         293.940002      -6.636690             NaN   
3778                   NaN         297.809998      -5.512426             NaN   

      Less_than_0 Ticker  
4012          NaN   NVDA  
4013          NaN   NVDA  
4014          NaN   NVDA  
4015          NaN   NVDA  
4016          NaN   NVDA  
...           ...    ...  
3774    -4.123878   TSLA  
3775          NaN   TSLA  
3776          NaN   TSLA  
3777    -6.636690   TSLA  
3778    -5.512426   TSLA  

[18501 rows x 15 columns]

In [14]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px
import numpy as np

# Enhanced color palettes and styling
MODERN_COLORS = {
    'primary': '#2E86AB',      # Deep blue
    'secondary': '#A23B72',    # Purple-pink
    'success': '#F18F01',      # Orange
    'warning': '#C73E1D',      # Red
    'accent': '#6A994E',       # Green
    'neutral': '#495057',      # Dark gray
    'background': '#F8F9FA',   # Light gray
    'grid': '#E9ECEF'         # Light grid
}

# Extended color palette for multiple tickers
TICKER_COLORS = [
    '#2E86AB', '#2E86AB', '#2E86AB', '#2E86AB', '#2E86AB', 
    '#2E86AB', '#2E86AB', '#2E86AB', '#2E86AB', '#2E86AB'
]

def create_modern_dashboard_style(df_mag_7, df_historical_data, moving_average):
    """Create a modern dashboard-style visualization with shaded areas between price and MA"""
    
    tickers = df_mag_7['Ticker'].unique()
    rows, cols = 7, 1
    
    fig = make_subplots(
        rows=rows, cols=cols,
        subplot_titles=[f'<b>{ticker}</b>' for ticker in tickers[:rows*cols]],
        horizontal_spacing=0.04,  
        vertical_spacing=0.03,   
        specs=[[{"type": "scatter"} for _ in range(cols)] for _ in range(rows)]
    )
    
    for i, ticker in enumerate(tickers[:rows*cols]):
        row = (i // cols) + 1
        col = (i % cols) + 1
        
        ticker_data = df_historical_data[df_historical_data['Ticker'] == ticker].copy()
        base_color = TICKER_COLORS[i % len(TICKER_COLORS)]
        
        # Assume we have 'Close' price column - adjust if your column name is different
        # If you don't have Close price, you might need to add it to your data
        price_column = 'Close'  # Change this to match your actual price column name
        ma_column = f'{moving_average}DMA'
        
        # Add the moving average line first (baseline for fills)
        fig.add_trace(
            go.Scatter(
                x=ticker_data['Date'], 
                y=ticker_data[ma_column],
                mode='lines',
                name=f'{moving_average}D MA',
                line=dict(
                    color=base_color, 
                    width=2,
                    shape='spline'
                ),
                showlegend=True if i == 0 else False,
                legendgroup=f'ma_{moving_average}',
                hovertemplate=f'<b>{ticker} - {moving_average}D MA</b><br>' +
                             'Date: %{x}<br>' +
                             f'{moving_average}D MA: %{{y:$,.2f}}<br>' +
                             '<extra></extra>'
            ),
            row=row, col=col
        )
        
        # Create separate traces for areas above and below MA
        # First, identify periods where price > MA
        above_ma_mask = ticker_data[price_column] > ticker_data[ma_column]
        below_ma_mask = ticker_data[price_column] <= ticker_data[ma_column]
        
        # For areas where price > MA (green fill)
        if above_ma_mask.any():
            # Create arrays with MA values where price <= MA, and price values where price > MA
            y_upper_green = ticker_data[price_column].where(above_ma_mask, ticker_data[ma_column])
            y_lower_green = ticker_data[ma_column]
            
            fig.add_trace(
                go.Scatter(
                    x=ticker_data['Date'],
                    y=y_upper_green,
                    mode='lines',
                    line=dict(width=0),
                    showlegend=False,
                    hoverinfo='skip'
                ),
                row=row, col=col
            )
            
            fig.add_trace(
                go.Scatter(
                    x=ticker_data['Date'],
                    y=y_lower_green,
                    mode='lines',
                    line=dict(width=0),
                    fill='tonexty',
                    fillcolor='rgba(106, 153, 78, 0.4)',  # Green with transparency
                    name='Above MA' if i == 0 else '',
                    showlegend=True if i == 0 else False,
                    legendgroup='above_ma',
                    hoverinfo='skip'
                ),
                row=row, col=col
            )
        
        # For areas where price <= MA (red fill)
        if below_ma_mask.any():
            # Create arrays with price values where price <= MA, and MA values as baseline
            y_upper_red = ticker_data[ma_column]
            y_lower_red = ticker_data[price_column].where(below_ma_mask, ticker_data[ma_column])
            
            fig.add_trace(
                go.Scatter(
                    x=ticker_data['Date'],
                    y=y_upper_red,
                    mode='lines',
                    line=dict(width=0),
                    showlegend=False,
                    hoverinfo='skip'
                ),
                row=row, col=col
            )
            
            fig.add_trace(
                go.Scatter(
                    x=ticker_data['Date'],
                    y=y_lower_red,
                    mode='lines',
                    line=dict(width=0),
                    fill='tonexty',
                    fillcolor='rgba(199, 62, 29, 0.4)',  # Red with transparency
                    name='Below MA' if i == 0 else '',
                    showlegend=True if i == 0 else False,
                    legendgroup='below_ma',
                    hoverinfo='skip'
                ),
                row=row, col=col
            )
        
        # Add the actual price line on top for clear visualization
        fig.add_trace(
            go.Scatter(
                x=ticker_data['Date'], 
                y=ticker_data[price_column],
                mode='lines',
                name='Stock Price',
                line=dict(
                    color='#2c3e50',  # Dark color for price line
                    width=3,
                    shape='spline'
                ),
                showlegend=True if i == 0 else False,
                legendgroup='price',
                hovertemplate=f'<b>{ticker} - Stock Price</b><br>' +
                             'Date: %{x}<br>' +
                             f'Price: %{{y:$,.2f}}<br>' +
                             '<extra></extra>'
            ),
            row=row, col=col
        )
        
        # Add your existing greater than and less than MA lines (optional - you can remove if too cluttered)
        fig.add_trace(
            go.Scatter(
                x=ticker_data['Date'], 
                y=ticker_data[f'Greater_than_{moving_average}_DMA'],
                mode='lines',
                name=f'{ticker} - Above {moving_average}DMA',
                line=dict(
                    color=MODERN_COLORS['accent'],  # Green for above
                    width=1,
                    dash='dot',
                    shape='spline'
                ),
                showlegend=True if i == 0 else False,
                legendgroup=f'above_ma_line_{moving_average}',
                opacity=0.7,
                hovertemplate=f'<b>{ticker} - Above {moving_average}D MA</b><br>' +
                             'Date: %{x}<br>' +
                             f'Above MA: %{{y:$,.2f}}<br>' +
                             '<extra></extra>'
            ),
            row=row, col=col
        )
        
        fig.add_trace(
            go.Scatter(
                x=ticker_data['Date'], 
                y=ticker_data[f'Less_than_{moving_average}_DMA'],
                mode='lines',
                name=f'{ticker} - Below {moving_average}DMA',
                line=dict(
                    color=MODERN_COLORS['warning'],  # Red for below
                    width=1,
                    dash='dash',
                    shape='spline'
                ),
                showlegend=True if i == 0 else False,
                legendgroup=f'below_ma_line_{moving_average}',
                opacity=0.7,
                hovertemplate=f'<b>{ticker} - Below {moving_average}D MA</b><br>' +
                             'Date: %{x}<br>' +
                             f'Below MA: %{{y:$,.2f}}<br>' +
                             '<extra></extra>'
            ),
            row=row, col=col
        )
        
        # Update individual subplot styling
        fig.update_xaxes(
            showgrid=True,
            gridwidth=0.5,
            gridcolor='rgba(128,128,128,0.1)',
            showticklabels=True,
            tickfont=dict(size=10),
            row=row, col=col
        )
        
        fig.update_yaxes(
            showgrid=True,
            gridwidth=0.5,
            gridcolor='rgba(128,128,128,0.1)',
            tickformat='$,.0f',
            tickfont=dict(size=10),
            row=row, col=col
        )
    
    fig.update_layout(
        height=300*rows,
        title={
            'text': f'<b>Portfolio Dashboard with Price vs {moving_average}D Moving Average</b><br>' +
                   f'<span style="font-size:16px; color:#6c757d">Shaded Areas Show Price Above (Green) and Below (Red) MA</span>',
            'x': 0.5,
            'xanchor': 'center',
            'font': {'size': 28, 'family': 'Arial, sans-serif'}
        },
        plot_bgcolor='white',
        paper_bgcolor='#f8f9fa',
        margin=dict(t=120, b=60, l=40, r=40),
        font=dict(family="Arial, sans-serif", size=12, color="#2c3e50"),
        legend=dict(
            orientation="h",
            yanchor="bottom",
            y=-0.15,
            xanchor="center",
            x=0.5,
            bgcolor='rgba(255,255,255,0.9)',
            bordercolor='rgba(128,128,128,0.2)',
            borderwidth=1
        )
    )
    
    # Style subplot titles
    for annotation in fig.layout.annotations:
        annotation.update(
            font=dict(size=14, color=MODERN_COLORS['primary'], family="Arial, sans-serif")
        )
    
    return fig

fig_dashboard = create_modern_dashboard_style(df_mag_7, df_historical_data, moving_average)
fig_dashboard.show()